In [3]:
import bamboolib as bam
import pandas as pd
import numpy as np
import os

In [59]:
# fájl beolvasása

working_directory = os.getcwd()

file_path = os.path.join(working_directory, 'globalterrorismdb_0522dist.xlsx')

In [60]:
# az alap dataframe

df_base = pd.read_excel(file_path)

df_base

             eventid  iyear  imonth  iday           approxdate  extended  \
0       197000000001   1970       7     2                  NaN         0   
1       197000000002   1970       0     0                  NaN         0   
2       197001000001   1970       1     0                  NaN         0   
3       197001000002   1970       1     0                  NaN         0   
4       197001000003   1970       1     0                  NaN         0   
...              ...    ...     ...   ...                  ...       ...   
209701  202012310015   2020      12    31  2020-12-31 00:00:00         0   
209702  202012310016   2020      12    31  2020-12-31 00:00:00         0   
209703  202012310017   2020      12    31                  NaN         0   
209704  202012310018   2020      12    31                  NaN         0   
209705  202012310019   2020      12    31                  NaN         1   

       resolution  country         country_txt  region  ... addnotes  \
0             N

In [61]:
# a tisztított dataframe

parquet_path = os.path.join(working_directory, 'df_survived.parquet.gzip')
df_survived_reduced = pd.read_parquet(parquet_path, engine='pyarrow')
df_survived_reduced = df_survived_reduced.drop(columns=['eventid', 'ishostkid', 'imonth', 'iday', 'country', 'region', 'provstate', 'city', 'summary', 'crit1', 'crit2', 'crit3', 'doubtterr', 'attacktype1', 'attacktype3', 'attacktype2', 'targtype1', 'targsubtype1', 'corp1', 'natlty1', 'guncertain1', 'nperpcap', 'weaptype1', 'nkillus', 'nkillter', 'nwoundus', 'nwoundte', 'nhostkidus', 'hostkidoutcome', 'scite1', 'INT_ANY', 'INT_MISC', 'INT_IDEO', 'INT_LOG', 'dbsource'])

df_survived_reduced

       iyear  extended               country_txt                   region_txt  \
2       1970         0                 Venezuela                South America   
4       1970         1                 Guatemala  Central America & Caribbean   
5       1970         1                    Brazil                South America   
6       1970         1                  Ethiopia           Sub-Saharan Africa   
8       1970         1        Dominican Republic  Central America & Caribbean   
...      ...       ...                       ...                          ...   
16557   2010         1  Central African Republic           Sub-Saharan Africa   
16558   2010         0               Philippines               Southeast Asia   
16559   2010         1                     Kenya           Sub-Saharan Africa   
16564   2010         1                  Pakistan                   South Asia   
16568   2011         1                    Turkey   Middle East & North Africa   

        latitude   longitud

In [12]:
# a numerikus változók közti korreláció

bam.correlations(df_survived_reduced)

TabSection(children=(BrowserCheck(), HBox(children=(Tab(closable=False, title='correlations', _dom_classes=('b…

In [57]:
import plotly.graph_objs as go
go.Figure(
    data=[go.Histogram(x=df_survived_reduced["survived"], xbins={"start": 0.0, "end": 1.0, "size": 0.06})],
    layout=go.Layout(title="A survived változó hisztogramja", yaxis={"title": "Esetszám"}, bargap=0.05),
    )

In [14]:
# az nhostkid változó leíró stat-ja

bam.plot(df_survived_reduced, 'nhostkid')

TabSection(children=(BrowserCheck(), HBox(children=(Tab(closable=False, title='plot', _dom_classes=('bamboolib…

In [15]:
# az nreleased változó leíró stat-ja

bam.plot(df_survived_reduced, 'nreleased')

TabSection(children=(BrowserCheck(), HBox(children=(Tab(closable=False, title='plot', _dom_classes=('bamboolib…

In [17]:
# évente ennyi eset volt, ami a "vizsgált részhalmazba esik"
# tehát hijacking, hostage taking (barricade vagy kidnapping)

fig = px.histogram(df_survived_reduced, x='iyear', y='survived', histfunc='count')
fig.update_layout(
    title="Az esetek száma az adott évben",
    xaxis_title="Év",
    yaxis_title="Esetszám"
)
fig

In [28]:
# minden évben (kivéve 1993-at mert akkor nem volt a vizsgált
# részhalmazba eső eset) a survived maximuma 1,
# a survived minimuma pedig az adott évben:

fig = px.histogram(df_survived_reduced, x='iyear', y='survived', histfunc='min', range_x=(1970, 2020))
fig.update_layout(
    title="A survived változó minimuma az adott évben",
    xaxis_title="Év",
    yaxis_title="min of surivived"
)
fig

In [40]:
# évenként a survived átlaga

fig = px.histogram(df_survived_reduced, x='iyear', y='survived', histfunc='avg', range_x=(1970, 2020))
fig.update_layout(
    title="A survived változó átlaga az adott évben",
    xaxis_title="Év",
    yaxis_title="avg of surivived"
)
fig

In [30]:
# az előző kettőhöz kapcsolódóan survived évenként
# boxplotként, annyira nem átlátható

fig = px.box(df_survived_reduced, x='iyear', y='survived')
fig.update_layout(
    title="A survived változó boxplotja az adott évben",
    xaxis_title="Év",
    yaxis_title="surivived"
)
fig

In [54]:
# régiónként és évenként a survived átlaga
# a 0 jelentheti azt is, hogy ehhez a csempéhez
# nem tartozott adat

fig = px.density_heatmap(df_survived_reduced, x='iyear', y='region_txt', z='survived', histfunc='avg')
fig.update_layout(
    title="A survived átlaga",
    xaxis_title="Év",
    yaxis_title="Régió"
)
fig.layout.coloraxis.colorbar.title = 'survived átlaga'
fig

In [58]:
# treemap hogy hány eset volt a régiókban, országokban

fig = px.treemap(df_survived_reduced, path=['region_txt', 'country_txt'])
fig.update_layout(
    title="Treemap"
)
fig

In [36]:
# az előzőhöz képest ezen jobban látszik
# az egészhez való viszony

fig = px.pie(df_survived_reduced, names='region_txt')
fig.update_layout(
    title="Az esetek aránya a régiók között"
)
fig

In [39]:
# régiónként a survived minimuma mindehol 0
# (kivéve Australasia & Oceania: min=0.5), a max mindenhol 1

# régiónként a survived átlaga

fig = px.histogram(df_survived_reduced, x='region_txt', y='survived', histfunc='avg')
fig.update_xaxes(categoryorder='total descending')
fig.update_layout(
    title="A survived változó átlaga az adott régióban",
    xaxis_title="Régió",
    yaxis_title="avg of surivived"
)
fig

In [45]:
# az átlag survived az országokra

fig = px.histogram(df_survived_reduced, x='country_txt', y='survived', histfunc='avg')
fig.update_xaxes(categoryorder='total descending')
fig.update_layout(
    title="A survived változó átlaga az adott országban",
    xaxis_title="Ország",
    yaxis_title="avg of surivived"
)
fig

In [46]:
# attól, hogy magas az nhostkid és nreleased korrelációja,
# szerintem még nem tudunk semmit, mert az nreleased 
# max nhostkid lehet, és ezért nyilván az y=x görbe alatti
# részben lesz valahol, akár y=0 környékén is

fig = px.scatter(df_survived_reduced, x='nhostkid', y='nreleased')
fig

In [56]:
# ha a csoport neve a csökkenés előtti tartományhoz tartozó
# részben van, akkor mindenki túlélte

fig = px.histogram(df_survived_reduced, x='gname', y='survived', histfunc='min')
fig.update_xaxes(categoryorder='total descending')
fig.update_layout(
    title="A survived változó minimuma az adott szervezetre",
    xaxis_title="Csoport neve",
    yaxis_title="min of surivived"
)
fig

In [53]:
# ha volt öngyilkosság, akkor jóval többször
# volt ez része egy sorozatos támadásnak

fig = px.histogram(df_survived_reduced.dropna(subset=['multiple']), x='suicide', color='multiple', barnorm='fraction')
fig.update_layout(
    xaxis_title="Volt-e öngyilkosság",
    yaxis_title="",
    legend_title="Többszörös támadás volt-e",
)
fig